In [ ]:
import pandas as pd

# 수산물 데이터
file_path = "통합 식품영양성분DB_수산물_20220926.xlsx"
water_df = pd.read_excel(file_path)
water_df = water_df[water_df['에너지(㎉)'] != "-"]
water_df = water_df[['식품명', '에너지(㎉)']]
water_df['Classification'] = '수산물'

# 농축산물 데이터 (에너지(kcal) -> 에너지(㎉)로 변경)
file_path = "통합 식품영양성분DB_농축산물_20220926.xlsx"
AgLP_df = pd.read_excel(file_path)
AgLP_df = AgLP_df.rename(columns={'에너지(kcal)': '에너지(㎉)'})  # 열 이름 변경
AgLP_df = AgLP_df[['식품명', '에너지(㎉)']]
AgLP_df['Classification'] = '농축산물'

# 가공식품 데이터
file_path = "통합 식품영양성분DB_가공식품_20220922.xlsx"
Processed_df = pd.read_excel(file_path)
Processed_df_filtered = Processed_df[Processed_df['에너지(㎉)'] != "-"]
Processed_df_filtered = Processed_df_filtered[['식품명', '에너지(㎉)']]
Processed_df_filtered['Classification'] = '가공식품'

# 음식 데이터
file_path = "통합 식품영양성분DB_음식_20221205.xlsx"
food_df = pd.read_excel(file_path, header=3)  # 3번째 행을 컬럼명으로 설정
food_df = food_df[food_df['에너지(㎉)'] != "-"]
food_df = food_df[food_df['에너지(㎉)'] != " "]
food_df = food_df.dropna(subset=['에너지(㎉)'])

food_df.columns = food_df.columns.str.strip()
food_df_filtered = food_df[['식품명', '에너지(㎉)']]
food_df_filtered['Classification'] = '음식'

# 네 개의 데이터프레임을 합치기
merged_df = pd.concat([water_df, AgLP_df, Processed_df_filtered, food_df_filtered], ignore_index=True)

# 번호 매기기 (1부터 시작)
merged_df['food_num'] = merged_df.index + 1

In [81]:
merged_df = merged_df[['food_num'] + [col for col in merged_df.columns if col != 'food_num']]

In [89]:
merged_df = merged_df.rename(columns={'식품명': 'name', '에너지(㎉)': 'kcal', 'Classification': 'classification'})

In [92]:
merged_df.keys()

Index(['food_num', 'name', 'kcal', 'classification'], dtype='object')

In [86]:
len(water_df), len(AgLP_df), len(Processed_df_filtered), len(food_df_filtered)

(505, 3270, 77712, 7686)

In [93]:
merged_df.to_excel('데이터 정제 및 통합본(농,수,음,가).xlsx', index=False, engine='openpyxl')

In [110]:
merged_df

food_num               name kcal classification
0             1               가다랑어  127            수산물
1             2  가다랑어-레토르트식품(기름담금)  175            수산물
2             3     가다랑어-통조림(기름담금)  209            수산물
3             4             가다랑어-포  372            수산물
4             5                가라지   78            수산물
...         ...                ...  ...            ...
89168     89169      <아내의 식탁>짜.수.치  251             음식
89169     89170   <아내의 식탁>바질베스토감바스  324             음식
89170     89171    <아내의 식탁>밀푀유스키야키  110             음식
89171     89172     <파빌리온>양갈비 스테이크  177             음식
89172     89173          할라피뇨 통살버거  631             음식

[89173 rows x 4 columns]

In [94]:
merged_df['kcal']

0        127
1        175
2        209
3        372
4         78
        ... 
89168    251
89169    324
89170    110
89171    177
89172    631
Name: kcal, Length: 89173, dtype: object

In [1]:
import pymysql

# DB 연결
conn = pymysql.connect(
    host='localhost',  # DB 서버 주소
    user='root',  # 사용자 이름
    password='koyuko1870!',  # 비밀번호
    port=3307,
    database='madang',  # 데이터베이스 이름
    charset='utf8'
)

cursor = conn.cursor()

# 테이블 생성 SQL
create_table_query = """
CREATE TABLE IF NOT EXISTS `food` (
  `food_num` int NOT NULL,
  `classification` varchar(20) DEFAULT NULL,
  `foodname` varchar(100) CHARACTER SET utf8mb4 COLLATE utf8mb4_0900_ai_ci DEFAULT NULL,
  `kcal` FLOAT DEFAULT NULL,
  PRIMARY KEY (`food_num`)
)
"""

# 쿼리 실행
cursor.execute(create_table_query)

# 변경 사항 저장
conn.commit()

# 연결 종료
cursor.close()
conn.close()

print("food 테이블이 생성되었습니다.")

food 테이블이 생성되었습니다.


In [3]:
import pandas as pd

In [4]:
# 엑셀 파일 열기``
file_path = '데이터 정제 및 통합본(농,수,음,가).xlsx'
df = pd.read_excel(file_path, engine='openpyxl')

# 'data' 변수에 저장할 형태로 변환
data = [tuple(x) for x in df[['food_num', 'classification', 'name', 'kcal']].values]

In [8]:
# 엑셀 파일 열기
file_path = '데이터 정제 및 통합본(농,수,음,가).xlsx'
df = pd.read_excel(file_path, engine='openpyxl')
# 'data' 변수에 저장할 형태로 변환
data = [tuple(x) for x in df[['food_num', 'classification', 'name', 'kcal']].values]

In [10]:
print(data[7139])  # 0-indexed, so row 7140 corresponds to index 7139

(7140, '가공식품', '알렌스 버터필드 슈스트링 포테이토 스틱', '52.5')


In [ ]:
import pymysql

# DB 연결
conn = pymysql.connect(
    host='localhost',  # DB 서버 주소
    user='root',  # 사용자 이름
    password='koyuko1870!',  # 비밀번호
    port=3307,
    database='madang',  # 데이터베이스 이름
    charset='utf8'
)

cursor = conn.cursor()


# 데이터 삽입 SQL
insert_query = """
INSERT INTO food (food_num, classification, foodname, kcal)
VALUES (%s, %s, %s, %s)
"""

# 데이터 삽입 실행
cursor.executemany(insert_query, data)

# 변경 사항 커밋
conn.commit()

# 연결 종료
cursor.close()
conn.close()

print("데이터가 성공적으로 삽입되었습니다.")

DataError: (1265, "Data truncated for column 'kcal' at row 7140")

In [11]:
cursor = conn.cursor()

# 데이터 삽입 SQL
insert_query = """
INSERT INTO food (food_num, classification, foodname, kcal)
VALUES (%s, %s, %s, %s)
"""

# 데이터 삽입 실행
for row in data:
    try:
        cursor.execute(insert_query, row)
    except pymysql.MySQLError as e:
        # 오류 발생 시 해당 행을 출력하고 계속 진행
        print(f"Error inserting row: {row}")
        print(f"Error: {e}")
        continue  # 오류가 발생하면 해당 행을 건너뜀

# 변경 사항 커밋
conn.commit()

# 연결 종료
cursor.close()
conn.close()

print("데이터가 성공적으로 삽입되었습니다.")

Error inserting row: (1, '수산물', '가다랑어', '127')
Error: (1062, "Duplicate entry '1' for key 'food.PRIMARY'")
Error inserting row: (2, '수산물', '가다랑어-레토르트식품(기름담금)', '175')
Error: (1062, "Duplicate entry '2' for key 'food.PRIMARY'")
Error inserting row: (3, '수산물', '가다랑어-통조림(기름담금)', '209')
Error: (1062, "Duplicate entry '3' for key 'food.PRIMARY'")
Error inserting row: (4, '수산물', '가다랑어-포', '372')
Error: (1062, "Duplicate entry '4' for key 'food.PRIMARY'")
Error inserting row: (5, '수산물', '가라지', '78')
Error: (1062, "Duplicate entry '5' for key 'food.PRIMARY'")
Error inserting row: (6, '수산물', '가래상어', '99')
Error: (1062, "Duplicate entry '6' for key 'food.PRIMARY'")
Error inserting row: (7, '수산물', '가무락조개', '77')
Error: (1062, "Duplicate entry '7' for key 'food.PRIMARY'")
Error inserting row: (8, '수산물', '가물치', '86')
Error: (1062, "Duplicate entry '8' for key 'food.PRIMARY'")
Error inserting row: (9, '수산물', '가시망둑', '101')
Error: (1062, "Duplicate entry '9' for key 'food.PRIMARY'")
Error inserting r

In [16]:
# DB 연결
conn = pymysql.connect(
    host='localhost',  # DB 서버 주소
    user='root',  # 사용자 이름
    password='koyuko1870!',  # 비밀번호
    port=3307,
    database='madang',  # 데이터베이스 이름
    charset='utf8'
)
cursor = conn.cursor()

# 테이블에 저장된 행 수를 확인하는 SQL
count_query = "SELECT count(*) FROM food"

# 쿼리 실행
cursor.execute(count_query)

# 결과 가져오기
row_count = cursor.fetchone()[0]

# 결과 출력
print(f"food 테이블에 저장된 행의 수는 {row_count}개 입니다.")

# 연결 종료
cursor.close()
conn.close()

food 테이블에 저장된 행의 수는 89172개 입니다.
